<a href="https://colab.research.google.com/github/ritwikraha/computer-needs-glasses/blob/master/image-object-tracking/Object_Tracking_for_UFC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# Step 1: Set up the Colab environment
!pip install -q ultralytics
!pip install -q opencv-python-headless
!pip install -q moviepy
!pip install -q controlnet_aux

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 779.6/779.6 kB 13.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.3/21.3 MB 72.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 282.4/282.4 kB 5.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.2/43.2 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.0/510.0 kB 35.3 MB/s eta 0:00:00


In [ ]:
from ultralytics import YOLO, SAM
import cv2
from controlnet_aux import OpenposeDetector
import moviepy.editor as mpy
from google.colab import files
import numpy as np

/usr/local/lib/python3.10/dist-packages/controlnet_aux/mediapipe_face/mediapipe_face_common.py:7: UserWarning: The module 'mediapipe' is not installed. The package will have limited functionality. Please install it using the command: pip install 'mediapipe'
  warnings.warn(


In [ ]:
# Upload the video file
uploaded = files.upload()

# Define the video file path
video_path = list(uploaded.keys())[0]

Saving gathjevpoirier2.mp4 to gathjevpoirier2.mp4


In [ ]:
# Initialize the YOLOv8 model for object detection
detection_model = YOLO("yolov8n.pt")  # You can use any YOLOv8 model

# Initialize the SAM model for segmentation
sam_model = SAM("sam_b.pt")

# Initialize the YOLOv8 model for pose detection
pose_model = YOLO("yolov8n-pose.pt")

100%|██████████| 6.23M/6.23M [00:00<00:00, 289MB/s]


100%|██████████| 358M/358M [00:00<00:00, 404MB/s]


100%|██████████| 6.51M/6.51M [00:00<00:00, 373MB/s]


In [9]:
# Open the video file
cap = cv2.VideoCapture(video_path)
# Get the video writer initialized to save the output video
fourcc = cv2.VideoWriter_fourcc(*'XVID')
out = cv2.VideoWriter('output.avi', fourcc, 20.0, (int(cap.get(3)), int(cap.get(4))))

In [10]:
while(cap.isOpened()):
    ret, frame = cap.read()
    if ret:
        # Step 2: Detect bounding boxes of persons
        detection_results = detection_model(frame)

        # Find the two persons with the biggest bounding boxes
        biggest_boxes = []
        for result in detection_results:
            for i, bbox in enumerate(result.boxes.xyxy):
                if result.names[int(result.boxes.cls[i])] == "person":
                    # Calculate area of the bounding box
                    x1, y1, x2, y2 = map(int, bbox.cpu().numpy().tolist())
                    area = (x2 - x1) * (y2 - y1)
                    biggest_boxes.append((area, bbox.cpu().numpy().tolist()))

        # Sort detections based on area (descending order)
        biggest_boxes.sort(reverse=True)

        # Select the top two detections (if available)
        selected_boxes = biggest_boxes[:2]  # Grab the top 2 elements

        if selected_boxes:
            annotated_frame = np.zeros_like(frame)
            for person_box in selected_boxes:
                x1, y1, x2, y2 = person_box[1]

                # Step 3: Segment the person using SAM model
                mask_results = sam_model(frame, bboxes=[[x1, y1, x2, y2]])

                # Debug: print structure of mask_results (optional)
                # print("mask_results structure:", mask_results)

                # Extract the mask
                mask = mask_results[0].masks.data[0].cpu().numpy()

                # Apply mask to the frame
                segmented_frame = cv2.bitwise_and(frame, frame, mask=mask.astype(np.uint8))

                # Step 4: Run pose detection on the segmented person
                pose_results = pose_model(segmented_frame)

                # Draw keypoints on the black background frame
                for result in pose_results:
                    pose_annotated_frame = result.plot()
                    mask_inv = cv2.bitwise_not(mask.astype(np.uint8))
                    frame_bg = cv2.bitwise_and(annotated_frame, annotated_frame, mask=mask_inv)
                    person_fg = cv2.bitwise_and(pose_annotated_frame, pose_annotated_frame, mask=mask.astype(np.uint8))
                    annotated_frame = cv2.add(frame_bg, person_fg)

            # Write the frame into the output video
            out.write(annotated_frame)
        else:
            # If no person is detected, write the original frame
            out.write(np.zeros_like(frame))
    else:
        break

# Release the video capture and writer objects
cap.release()
out.release()


Streaming output truncated to the last 5000 lines.
0: 1024x1024 240.0ms
Speed: 6.3ms preprocess, 240.0ms inference, 0.2ms postprocess per image at shape (1, 3, 1024, 1024)

0: 384x640 1 person, 8.5ms
Speed: 2.2ms preprocess, 8.5ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 1024x1024 238.6ms
Speed: 6.2ms preprocess, 238.6ms inference, 0.2ms postprocess per image at shape (1, 3, 1024, 1024)

0: 384x640 1 person, 8.3ms
Speed: 2.2ms preprocess, 8.3ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 6 persons, 7.5ms
Speed: 2.2ms preprocess, 7.5ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 1024x1024 240.0ms
Speed: 5.9ms preprocess, 240.0ms inference, 0.2ms postprocess per image at shape (1, 3, 1024, 1024)

0: 384x640 1 person, 8.2ms
Speed: 2.1ms preprocess, 8.2ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 1024x1024 240.6ms
Speed: 6.2ms preprocess, 240.6ms inference, 0.2ms postprocess per

In [11]:
# Step 5: Display the processed video
output_video_path = 'output.avi'

# Convert the video to MP4 format to display in Colab
clip = mpy.VideoFileClip(output_video_path)
clip.write_videofile("output-ufc-generated.mp4")

Moviepy - Building video output-ufc-generated.mp4.
Moviepy - Writing video output-ufc-generated.mp4



Moviepy - Done !
Moviepy - video ready output-ufc-generated.mp4


In [13]:
from IPython.display import HTML
from base64 import b64encode

# Replace 'video.mp4' with the actual filename of your video
mp4 = open('output-ufc-generated.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()

# This creates the HTML code to display the video with controls
html = HTML("""
<video width=400 controls>
  <source src="%s" type="video/mp4">
</video>
""" % data_url)

# Display the video in the Colab notebook
display(html)


In [14]:
from google.colab import files

# Replace 'your_file.txt' with the actual filename you want to download
# filename = "output-ufc-generated.mp4"
# filename = "output-ufc-generated.mp4"
filename = "output-ufc-generated.mp4"


# Download the file
files.download(filename)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>